# HRRR Dashboard
The High Resolution Rapid Refresh (HERR, pronouned "her") is the highest resolution (2.5km) weather forecast for the entire USA.  Here we investigate the output, accessing the forecast from [Unidata's THREDDS server](http://thredds.ucar.edu) and visualizing the results using the [pyviz](pyviz.org) tools. 

In [17]:
import xarray as xr

In [18]:
ds = xr.open_dataset('http://thredds.ucar.edu/thredds/dodsC/grib/NCEP/HRRR/CONUS_2p5km/Best')

Drop the "reftime" coordinate variables, as hvplot has trouble with this

In [3]:
ds = ds.drop([coord for coord in ds.coords if 'reftime' in coord])

Find all the data variables that depend on time (and are not time `bounds`)

In [4]:
time_vars = []
for var in ds.data_vars:
    if len(ds[var].dims) > 0:
        if 'time' in ds[var].dims[0] and not 'bounds' in var:
            time_vars.append(var)

Import the [pyviz](http://pyviz.org) tools we need

In [5]:
from cartopy import crs as ccrs
import hvplot.xarray
import holoviews as hv
from geoviews import tile_sources as gvts
import panel as pn

Create widget for variable selection

In [6]:
var_select = pn.widgets.Select(name='HRRR Variables:', options=time_vars, 
                               value='Temperature_height_above_ground')

Create widget for basemap selection

In [7]:
map_select = pn.widgets.Select(name='Basemap:', options=gvts.tile_sources, value=gvts.OSM)                                                    

Create a color mesh plot in Lambert Conformal coordinates with hvplot and cartopy

In [8]:
globe = ccrs.Globe(ellipse='sphere', semimajor_axis=ds.LambertConformal_Projection.earth_radius)
lat0 = ds.LambertConformal_Projection.latitude_of_projection_origin
lon0 = ds.LambertConformal_Projection.longitude_of_central_meridian
lat1 = ds.LambertConformal_Projection.standard_parallel

Convert coordinates from kilometers to meters so that projection will work

In [9]:
ds['x'].values = ds['x'].values*1000.
ds['y'].values = ds['y'].values*1000.

In [10]:
crs = ccrs.LambertConformal(central_latitude=lat0, central_longitude=lon0,
                            standard_parallels=(lat0,lat1), globe=globe)

 We specify the `groupby` parameter in the `hvplot` command to be the list of dimensions that remains after we remove Y and X: `ds[var].dims[:-2]`, which handles variables with either dimensions [T, Y, X] or [T, Z, Y, X],

In [11]:
def plot(var=None, tiles=None):
    var = var or var_select.value
    tiles = tiles or map_select.value
    mesh = ds[var].hvplot.quadmesh(x='x', y='y', rasterize=True, crs=crs, title=var,
                                   width=600, height=400, groupby=list(ds[var].dims[:-2]), cmap='jet')
    return (mesh.opts(alpha=0.7) * tiles).opts(active_tools=['wheel_zoom', 'pan'])

In [12]:
def on_var_select(event):
    var = event.obj.value
    col[-1] = plot(var=var)

In [13]:
def on_map_select(event):
    tiles = event.obj.value
    col[-1] = plot(tiles=tiles)

In [14]:
var_select.param.watch(on_var_select, parameter_names=['value']);
map_select.param.watch(on_map_select, parameter_names=['value']);

We change the default slider to a selection widget for the 'time' dimension.  See https://stackoverflow.com/a/54912917/2005869

In [15]:
col = pn.Column(var_select, map_select, 
                pn.holoviews.HoloViews(plot(var_select.value), 
                             widgets={ds[var_select.value].dims[0]: pn.widgets.Select}).layout)

We use `.servable()` here not only to display the panel object, but makes it servable via:  `panel serve HRRR_Dashboard.ipynb`

In [16]:
col.servable()

Column
    [0] Select(name='HRRR Variables:', options=OrderedDict([('Vertical_v-...]), value='Temperature_height_above_...)
    [1] Select(name='Basemap:', options={'CartoDark': :WMTS   [Lon...}, value=:WMTS   [Longitude,L...)
    [2] Row
        [0] HoloViews(DynamicMap, widgets={'time': <class '...})
        [1] WidgetBox
            [0] Select(name='GRIB forecast o..., options=OrderedDict([('2019-02-24 ...]), value=numpy.datetime64('2019-02-...)
            [1] Select(name='Specified height l..., options=OrderedDict([('2.0', ...]), value=2.0)